In [1]:
import os
import folium

print(folium.__version__)

0.8.3+52.g2758dc7.dirty


# How to draw a GeoPandas.GeoDataFrame into folium

GeoPandas is a project to add support for geographic data to [pandas](http://pandas.pydata.org) objects.
(See https://github.com/geopandas/geopandas)

It provides (among other cool things) a `GeoDataFrame` object that represents a Feature collection.
When you have one, you may be willing to use it on a folium map. Here's the simplest way to do so.

In this example, we'll use the same file as GeoPandas demo ; it's containing
[the boroughs of New York City](http://www.nyc.gov/html/dcp/download/bytes/nybb_14aav.zip).

In [2]:
import geopandas


url = 'https://raw.githubusercontent.com/python-visualization/folium/master/examples/data'
nybb = f'{url}/nybb.zip'
boros = geopandas.read_file(nybb)

boros

BoroCode       BoroName     Shape_Leng    Shape_Area  \
0         5  Staten Island  330454.175933  1.623847e+09   
1         3       Brooklyn  741227.337073  1.937810e+09   
2         4         Queens  896875.396449  3.045079e+09   
3         1      Manhattan  358400.912836  6.364308e+08   
4         2          Bronx  464475.145651  1.186822e+09   

                                            geometry  
0  (POLYGON ((970217.0223999023 145643.3322143555...  
1  (POLYGON ((1021176.479003906 151374.7969970703...  
2  (POLYGON ((1029606.076599121 156073.8142089844...  
3  (POLYGON ((981219.0557861328 188655.3157958984...  
4  (POLYGON ((1012821.805786133 229228.2645874023...

To create a map with these features, simply put them in a `GeoJson`:

In [3]:
m = folium.Map([40.7, -74], zoom_start=10, tiles='cartodbpositron')

folium.GeoJson(boros).add_to(m)

m.save(os.path.join('results', 'geopandas_0.html'))

m

Quite easy.

Well, you can also take advantage of your `GeoDataFrame` structure to set the style of the data. For this, just create a column `style` containing each feature's style in a dictionnary.

In [4]:
boros['style'] = [
    {'fillColor': '#ff0000', 'weight': 2, 'color': 'black'},
    {'fillColor': '#00ff00', 'weight': 2, 'color': 'black'},
    {'fillColor': '#0000ff', 'weight': 2, 'color': 'black'},
    {'fillColor': '#ffff00', 'weight': 2, 'color': 'black'},
    {'fillColor': '#00ffff', 'weight': 2, 'color': 'black'},
]

boros

BoroCode       BoroName     Shape_Leng    Shape_Area  \
0         5  Staten Island  330454.175933  1.623847e+09   
1         3       Brooklyn  741227.337073  1.937810e+09   
2         4         Queens  896875.396449  3.045079e+09   
3         1      Manhattan  358400.912836  6.364308e+08   
4         2          Bronx  464475.145651  1.186822e+09   

                                            geometry  \
0  (POLYGON ((970217.0223999023 145643.3322143555...   
1  (POLYGON ((1021176.479003906 151374.7969970703...   
2  (POLYGON ((1029606.076599121 156073.8142089844...   
3  (POLYGON ((981219.0557861328 188655.3157958984...   
4  (POLYGON ((1012821.805786133 229228.2645874023...   

                                               style  
0  {'fillColor': '#ff0000', 'weight': 2, 'color':...  
1  {'fillColor': '#00ff00', 'weight': 2, 'color':...  
2  {'fillColor': '#0000ff', 'weight': 2, 'color':...  
3  {'fillColor': '#ffff00', 'weight': 2, 'color':...  
4  {'fillColor': '#00ffff', 'weight': 2, 'color':...

In [5]:
m = folium.Map([40.7, -74], zoom_start=10, tiles='cartodbpositron')

folium.GeoJson(boros).add_to(m)

m.save(os.path.join('results', 'geopandas_1.html'))

m

Folium should work with any object that implements the `__geo_interface__` but be aware that sometimes you may need to convert your data to `epsg='4326'` before sending it to `folium`.

In [6]:
import fiona
import shapely


fname = f'{url}/2014_08_05_farol.gpx'
with fiona.open(fname, 'r', layer='tracks') as records:
    tracks = [
        shapely.geometry.shape(record['geometry']) for record in records
    ]

track = tracks[0]

m = folium.Map(tiles='cartodbpositron')
folium.GeoJson(track).add_to(m)

m.fit_bounds(m.get_bounds())

m.save(os.path.join('results', 'geopandas_2.html'))

m